In [2]:
import json
import os

import folium
import shapefile

### Conversão do arquivo Shapefile "limite_municipio.shp" para GeoJSON:

In [5]:
reader = shapefile.Reader("data/shp/AP_Municipios_2022.dbf")
fields = reader.fields[1:]
field_names = [field[0] for field in fields]
buffer = []
for sr in reader.shapeRecords():
    atr = dict(zip(field_names, sr.record))
    geom = sr.shape.__geo_interface__
    buffer.append(dict(type="Feature", geometry=geom, properties=atr))

In [6]:
geojson = open("data/geojson/limite_municipio.geojson", "w")
geojson.write(json.dumps({"type": "FeatureCollection", "features": buffer}, indent=2) + "\n")
geojson.close()

### Exibição no Leaflet:

In [15]:
lat, lng = 2.05108,  -50.7945
zoom_start = 7

In [92]:
import pandas as pd
cidades_df = pd.read_csv('cidades_amapa.csv')
dados_df = pd.read_csv('dados_ibge_amapa.csv')

merged = pd.merge(cidades_df, dados_df, how='inner', on='Municipio_Complete')

df = merged.query("Indicador == '1.1.4: Proporção de atendimentos odontológicos de urgência na demanda espontânea' and Quadrimestre == '2021-Q1'")

# Split the 'Coordinates' column into 'Latitude' and 'Longitude'
df[['Latitude', 'Longitude']] = df['lat__long'].str.split(',', expand=True)

# Convert Latitude and Longitude to float
df['Latitude'] = df['Latitude'].astype(float)
df['Longitude'] = df['Longitude'].astype(float)

def invert_nulo(value):
    if value == 1:
        return 0
    else:
        return 1

df['nulo_invertido'] = df['Nulo'].apply(invert_nulo)

C:\Users\julia\AppData\Local\Temp\ipykernel_11268\4246681272.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[['Latitude', 'Longitude']] = df['lat__long'].str.split(',', expand=True)
C:\Users\julia\AppData\Local\Temp\ipykernel_11268\4246681272.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[['Latitude', 'Longitude']] = df['lat__long'].str.split(',', expand=True)
C:\Users\julia\AppData\Local\Temp\ipykernel_11268\4246681272.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy o

In [89]:
m = folium.Map(location=[lat, lng], tiles="OpenStreetMap", zoom_start=zoom_start)
folium.Choropleth(geo_data=text, data = df, columns=['ibge_novo_7dig', 'nulo_invertido'], key_on='feature.properties.CD_MUN', fill_color='RdYlGn', legend_name=df['Indicador'].iloc[0]).add_to(m)
m

In [111]:
from pandasql import sqldf
query = """ 
    SELECT Municipio_Complete, SUM(Nulo) as soma, ibge_novo_7dig
    FROM merged
    GROUP BY Municipio_Complete
"""
resultado = sqldf(query, locals())

m = folium.Map(location=[lat, lng], tiles="OpenStreetMap", zoom_start=zoom_start)
for index, row in dados_df.iterrows():
    latitude = row['lat__long'].split(',')[0]
    longitude = row['lat__long'].split(',')[1]
    folium.Marker(location=[latitude,longitude], popup = row['Municipio_Complete']).add_to(m)
folium.Choropleth(geo_data=text, data = resultado, columns=['ibge_novo_7dig', 'soma'], key_on='feature.properties.CD_MUN', fill_color='Reds', legend_name="Quantidade de nulos").add_to(m)
m

Municipio_Complete  soma  ibge_novo_7dig
0                     Amapá, Amapá, AP, Brasil   581         1600105
1                  Calçoene, Amapá, AP, Brasil   574         1600204
2                    Cutias, Amapá, AP, Brasil   572         1600212
3            Ferreira Gomes, Amapá, AP, Brasil   727         1600238
4                   Itaubal, Amapá, AP, Brasil   760         1600253
5          Laranjal Do Jari, Amapá, AP, Brasil   460         1600279
6                    Macapá, Amapá, AP, Brasil   334         1600303
7                   Mazagão, Amapá, AP, Brasil   604         1600402
8                  Oiapoque, Amapá, AP, Brasil   535         1600501
9   Pedra Branca Do Amapari, Amapá, AP, Brasil   547         1600154
10             Porto Grande, Amapá, AP, Brasil   645         1600535
11                 Pracuúba, Amapá, AP, Brasil   801         1600550
12                  Santana, Amapá, AP, Brasil   332         1600600
13           Serra Do Navio, Amapá, AP, Brasil   690         1600055
14          Tartarugalzinho, Amapá, AP, Brasil   489         1600709
15          Vitória Do Jari, Amapá, AP, Brasil   557         1600808